In [1]:
import pandas as pd, numpy as np
import datetime as dt
from rapidfuzz import process, fuzz,utils
np.set_printoptions(threshold=np.inf)

In [2]:
pim_color = pd.read_csv('PIM_Color_Attributes_102523.csv')
gtin_itm_id = pd.read_csv('ITM_ID_GTIN_102523.csv')
pim_color['GTIN_NO'] = pim_color.ITM_ID.map(dict(zip(gtin_itm_id.ITM_ID, gtin_itm_id.GTIN_NO)))
#flavors_COM = pd.DataFrame(pim_flavors.groupby('COM_CD').apply(lambda x: '|'.join(x.Flavor_Code.unique())), columns= ['UNIQUE FLAVORS']).reset_index()

In [3]:
pim_df = pd.read_csv('PIM_DATA_W_TAG_DSC_110323.zip')

In [4]:
pim_load = pim_color.merge(pim_df, how = 'right', on = 'GTIN_NO')
# SCENT_VLU different from SCENT_CD
pim_load[pim_load.COLOR_VLU.notnull() & (pim_load.COLOR_VLU != pim_load.COLOR_CD)]\
.drop_duplicates(['COLOR_CD','COLOR_VLU'])[['COLOR_CD','COLOR_VLU']]

COLOR_CD        COLOR_VLU
262        MULTI_COLORED    MULTI-COLORED
701           LIGHT_PINK       LIGHT PINK
904          BROWN_BLACK      BROWN-BLACK
2463       METALLIC_GRAY    METALLIC GRAY
2910     METALLIC_SILVER  METALLIC SILVER
...                  ...              ...
4022691             GRAY    MULTI-COLORED
4022927             BLUE            BROWN
4025004           PURPLE    MULTI-COLORED
4250012              RED            BROWN
4971274      DARK_INDIGO      DARK INDIGO

[109 rows x 2 columns]

In [5]:
# USE _VLU if present, else use _CD
pim_load['COLOR'] = np.where(pim_load.COLOR_VLU.notnull(), pim_load.COLOR_VLU, pim_load.COLOR_CD)

In [6]:
pim_load['COLOR'] = pim_load.COLOR.fillna('NONE')

In [7]:
sorted(list(pim_load.COLOR.dropna().unique()))

['#1 NUDE',
 '3D CLOUD/GREY',
 '3D CLOUD/PINK',
 'A WHOLE LOTTA WARMTH',
 'ABALONE',
 'ABSTRACT ORANGE',
 'ABYSS',
 'AFRICAN NIGHTS',
 'AHOY',
 'AIRY',
 'ALL NIGHT FUCHSIA',
 'ALL SMILES',
 'ALPHABET',
 'ALWAYS APRICOT',
 'ALWAYS SIENNA',
 'AMARANTH',
 'AMBER',
 'AMETHYST',
 'AMETHYST BLACK',
 'AMETHYST CHROME',
 'ANCHORS AWAY & SAILOR STRIPES',
 'ANCHORS AWEIGH',
 'ANTI-REDNESS',
 'ANTIQUE',
 'ANTIQUE BRASS',
 'APPLE',
 'APPLE GREEN',
 'APRICOT',
 'APRICOT FANTASY',
 'AQUA',
 'AQUA DOT',
 'AQUA SEA WAVE',
 'AQUAMARINE',
 'ARMY GREEN',
 'ASH BLONDE',
 'ASH VENEER',
 'ASHEN',
 'ASSORTED',
 'ASSORTED BOYS',
 'ASSORTED COLORS',
 'ASSORTED GIRLS',
 'ATLANTA FALCONS',
 'AUSTIN',
 'AVIGNON',
 'AVOCADO',
 'AZALEA PINK',
 'AZURE',
 'B/W ARROWS & STRIPES',
 'B/W ARROWS - TINY POLKA DOTS',
 'B/W HOUNDSTOOTH & TINY POLKA DOTS',
 'B/W STARS & STRIPES',
 'BABY BLUE',
 'BANANA-PINEAPPLE',
 'BARBIE',
 'BARE MAXIMUM',
 'BARK',
 'BATMAN',
 'BAYBERRY',
 'BEACH ROSE',
 'BEACH WOOD',
 'BEDAZZLED BISCOTTI'

In [8]:
replacements = {          
 ',': ' ',
 '/': ' ',
 '>':' ',
'<': ' '}


In [10]:
### Remove substrings like 'CHOCOLATE' if 'CHOCOLATE CHIP' is also present as a top result
def remove_substrings(string_list):
    str_df = pd.DataFrame(string_list, columns= ['Sentence'])
    str_df['Word Length'] = str_df.Sentence.apply(lambda x: len(x.split(' ')))
    str_df['Drop'] = ''
    str_df.sort_values('Word Length', inplace= True)
    str_df.reset_index(drop = True, inplace= True)
    for j in range(len(str_df)):
        str_1 = str_df.Sentence.loc[j]
        for i in range(len(str_df)-(j +1)):
            str_2 = str_df.Sentence.loc[i+j+1]
            if str_1 in str_2: 
                str_df.Drop.loc[j] = 'Yes'
                break
        if len(str_df) <2: 
            break
    return str_df[str_df.Drop != 'Yes'].Sentence.tolist()

In [28]:
#MAtch using 'token set ratio' with threshold
def color_match(item, color_list_org, cutoff = 90):
    #devowelized = [devowelize(i) for i in flavor_list_org]
    #derepeated = [remove_adjacent_repititions(i) for i in flavor_list_org]
    color_list = color_list_org #+ extras#+ devowelized
    #flavor_list += derepeated
    #abbrev_maps = dict(zip(devowelized+ derepeated, flavor_list_org + flavor_list_org))
    color_no_spaces = [ i for i in color_list_org if not '' in i]
    color_with_spaces = [ i for i in color_list_org if i not in color_no_spaces]
    abbrev_maps = {}
    for i in color_no_spaces:
        for j in color_with_spaces:
            if j.replace(' ','') == i:
                abbrev_maps[i] = j
    matched = process.extract(item, color_list, score_cutoff= cutoff, scorer = fuzz.token_set_ratio, processor=utils.default_process, limit= 7)
    color_shortlist = [i[0] for i in matched]
    matched = [i for i in matched if i[0] in color_shortlist]
    if len( color_shortlist) >0:
        max_score = matched[0][1]
        final_match = [ i for i in matched if i[1]== max_score]
        match_list = [i[0] for i in final_match]
        match_list = [abbrev_maps[i] if i in abbrev_maps.keys() else i for i in match_list]
        rematched = process.extract(item, match_list,  scorer = fuzz.partial_ratio, processor=utils.default_process, limit = 5)
        re_max_score = rematched[0][1]
        final_rematch = [ i for i in rematched if i[1]== re_max_score]
        match_list =  remove_substrings([i[0] for i in final_rematch])
        match_list_ordered =[]
        for word in item.split(' '):#Ordering scents according to thair appearance in the description text
            for color_token in match_list:
                if word in color_token:
                    match_list_ordered.append(color_token)
                    continue
        if len(match_list_ordered) >0:
            match_list = pd.Series(match_list_ordered).drop_duplicates().tolist()
        else:
            match_list = pd.Series(match_list).drop_duplicates().tolist()
    
        
        matched = ' '.join(list(pd.Series(match_list)))
    else: 
        matched = 'OTHER'
    return matched

### Match within DPT

In [13]:
colors_DPT = pd.DataFrame(pim_load.groupby('DPT_DSC').apply(lambda x: '|'.join(x.COLOR.unique())), columns= ['UNIQUE COLORS']).reset_index()
color_DPT_DSCs = colors_DPT[~colors_DPT['UNIQUE COLORS'].apply(lambda x: set(x.split('|')).issubset({'NONE','OTHER'}))].DPT_DSC.unique()
len(color_DPT_DSCs)

64

In [15]:
colors_COM = pd.DataFrame(pim_load.groupby('COM_CD').apply(lambda x: '|'.join(x.COLOR.unique())), columns= ['UNIQUE COLORS']).reset_index()
color_COM_CDs = colors_COM[~colors_COM['UNIQUE COLORS'].apply(lambda x: set(x.split('|')).issubset({'NONE','OTHER'}))].COM_CD.unique()
len(color_COM_CDs)

425

In [16]:
colors_COM

COM_CD                                      UNIQUE COLORS
0       0.0                                               NONE
1       1.0                                        NONE|GOLDEN
2       2.0                                           NONE|RED
3       3.0                                               NONE
4       4.0                                               NONE
..      ...                                                ...
823   993.0  NONE|OTHER|BLACK|BLUE|DENIM|WHITE|OLIVE|PINK|B...
824   994.0                                               NONE
825   995.0  NONE|MULTI-COLORED|WHITE|YELLOW|ORANGE|RED|PUR...
826   997.0                                 NONE|MULTI-COLORED
827   998.0                                               NONE

[828 rows x 2 columns]

In [17]:
#Exclude COMS without color
pim_load = pim_load[pim_load.COM_CD.isin(color_COM_CDs)]

In [18]:
#Concatenate multiple item description fields
pim_load['MATCHING_DESCRIPTION'] = \
pim_load.ITM_LVL_DSC.fillna('') + ' ' + pim_load.VND_ECOM_DSC +' '+  pim_load.TAG_DSC.fillna('')

In [19]:
color_list = [i.replace('_',' ') for i in pim_load['COLOR'].unique() if not i in  ['OTHER','NONE']]

In [35]:
pim_colorful = pim_load[~pim_load.COLOR.isin(['NONE'])]
pim_colorful.DPT_DSC.value_counts()[:10]

FURN/HOME DEC     264255
HOUSEWARES        136057
GARDEN-OUTDOOR    135134
DOMESTICS          49477
SEASONAL           47788
CARDS              38910
TOYS               38013
SCHOOL/OFFICE      36785
HOME IMPRVMNT      25425
MENS WEAR          20958
Name: DPT_DSC, dtype: int64

In [34]:
pim_load[pim_load.DPT_DSC == 'HOUSEWARES']

ITM_ID_x COLOR_CD COLOR_VLU         GTIN_NO   ITM_ID_y  \
31               NaN      NaN       NaN    733652146078  743493691   
119              NaN      NaN       NaN    719812076096  743494857   
302      800090268.0    OTHER     OTHER    847539063980  743495492   
313              NaN      NaN       NaN  50011120243067  743498727   
536              NaN      NaN       NaN  20719812076090  743494862   
...              ...      ...       ...             ...        ...   
5274948  804511133.0  NATURAL   NATURAL    444800443832  747914388   
5275049          NaN      NaN       NaN     34223314064  747914700   
5275063  804511303.0     JADE      JADE     34223313753  747914707   
5275266  805167867.0     GRAY      GRAY    644637112523  748567548   
5275267          NaN      NaN       NaN    644637040673  748567551   

                                                  GTIN_NAM  PMY_DPT_CD  \
31       Hampton Forge™ Gourdon Satin - 20 Piece Flatwa...         3.0   
119                                              2160900N2         3.0   
302                                   Glass Herb Preserver         3.0   
313                     BISSELL Adapt Ion Pet Stick Vacuum         3.0   
536                                              2160900N2         3.0   
...                                                    ...         ...   
5274948                                                NaN         3.0   
5275049                           1/2 GAL LD RETRO PRP SGL         3.0   
5275063                        1/2 GAL LD 2 RETRO JADE SGL         3.0   
5275266                                                NaN         3.0   
5275267                                                NaN         3.0   

        PMY_DPT_DSC  REC_DPT_CD REC_DPT_DSC  ...     DPT_DSC COM_CD  \
31          DRUG/GM        87.0          GM  ...  HOUSEWARES  792.0   
119         DRUG/GM        87.0          GM  ...  HOUSEWARES  736.0   
302         DRUG/GM        87.0          GM  ...  HOUSEWARES  739.0   
313         DRUG/GM        87.0          GM  ...  HOUSEWARES  812.0   
536         DRUG/GM        87.0          GM  ...  HOUSEWARES  736.0   
...             ...         ...         ...  ...         ...    ...   
5274948     DRUG/GM        87.0          GM  ...  HOUSEWARES  739.0   
5275049     DRUG/GM        87.0          GM  ...  HOUSEWARES  245.0   
5275063     DRUG/GM        87.0          GM  ...  HOUSEWARES  245.0   
5275266     DRUG/GM        87.0          GM  ...  HOUSEWARES  739.0   
5275267     DRUG/GM        87.0          GM  ...  HOUSEWARES  735.0   

                            COM_DSC SUBCOM_CD            SUBCOM_DSC  \
31               DRINKWARE/FLATWARE   73550.0              FLATWARE   
119                       FOOD PREP   73531.0         GADGETS/TOOLS   
302                    FOOD STORAGE   76081.0   KITCHEN ACCESSORIES   
313      VACUUMS/STEAMERS/CHEMICALS   73564.0     VACUUMS/HAND VACS   
536                       FOOD PREP   73531.0         GADGETS/TOOLS   
...                             ...       ...                   ...   
5274948                FOOD STORAGE   76081.0   KITCHEN ACCESSORIES   
5275049                    BEVERAGE   73540.0  THERMAL BEVERAGEWARE   
5275063                    BEVERAGE   73540.0  THERMAL BEVERAGEWARE   
5275266                FOOD STORAGE   76081.0   KITCHEN ACCESSORIES   
5275267        DINNERWARE/SERVEWARE   73507.0       BASIC OPENSTOCK   

        ITM_LVL_DSC                                       VND_ECOM_DSC  \
31              NaN  Hampton Forge™ Gourdon Satin - 20 Piece Flatwa...   
119             NaN                    OXO SW COLANDER - GREEN HANDLES   
302             NaN                               Glass Herb Preserver   
313             NaN                 BISSELL Adapt Ion Pet Stick Vacuum   
536             NaN                    OXO SW COLANDER - GREEN HANDLES   
...             ...                                                ...   
5274948         NaN               Bee & Willow Bar Cart wi

In [32]:
#Match selected DPTs
display_cols = ['GTIN_NO','PMY_DPT_DSC','REC_DPT_DSC','DPT_DSC','COM_DSC','SUBCOM_DSC','VND_ECOM_DSC','ITM_LVL_DSC','COLOR_CURRENT','EXTRACTED_COLOR']
today = dt.datetime.today().strftime("%m%d%Y")

'''with pd.ExcelWriter("COLORS_"+ today+".xlsx") as writer:
    for dpt in ['TOYS']:#, 'PERSONAL CARE','PET','BEAUTY']:# Choose from scents_DPT.DPT_DSC.unique():
        print(dpt)
        pim_dpt = pim_load[pim_load.DPT_DSC == dpt]
        pim_dpt.rename(columns={'COLOR':'COLOR_CURRENT'}, inplace= True)
        pim_dpt['EXTRACTED_COLOR']  =  \
                       pim_dpt.MATCHING_DESCRIPTION.str.upper().replace(replacements, regex = True).apply(lambda x:color_match(x, color_list_org= color_list))# + [i.replace(" ","") for  i in  color_list]))   
        pim_dpt[display_cols].to_excel(writer, sheet_name= dpt.replace('/',' '))'''
for dpt in ['HOUSEWARES']:#, 'PERSONAL CARE','PET','BEAUTY']:# Choose from scents_DPT.DPT_DSC.unique():
    print(dpt)
    pim_dpt = pim_load[pim_load.DPT_DSC == dpt]
    pim_dpt.rename(columns={'COLOR':'COLOR_CURRENT'}, inplace= True)
    pim_dpt['EXTRACTED_COLOR']  =  \
                   pim_dpt.MATCHING_DESCRIPTION.str.upper().replace(replacements, regex = True).apply(lambda x:color_match(x, color_list_org= color_list))# + [i.replace(" ","") for  i in  scent_list]))   
    pim_dpt[display_cols].to_csv('COLOR_'+dpt+'_DPT.csv', index = None)

HOUSEWARES


C:\Users\iny8251\AppData\Local\Temp\ipykernel_1016\109882214.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pim_dpt.rename(columns={'COLOR':'COLOR_CURRENT'}, inplace= True)
C:\Users\iny8251\AppData\Local\Temp\ipykernel_1016\540123340.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  str_df.Drop.loc[j] = 'Yes'
C:\Users\iny8251\AppData\Local\Temp\ipykernel_1016\540123340.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  str_d

beauty = pd.read_csv('BEAUTY_updated_111423.csv')

pd.DataFrame(beauty.groupby('COM_DSC').apply(lambda x:[i for i in scent_list if i in  x.EXTRACTED_SCENT.unique()]), columns= ['UNIQUE_SCENTS_WITHIN_THIS_CATEGORY'])\
.reset_index(drop = False).to_csv('BEAUTY_UNIQUE_SCENTS_IN_COMS.csv', index = None)

pd.DataFrame(beauty.groupby('SUBCOM_DSC').apply(lambda x:[i for i in scent_list if i in  x.EXTRACTED_SCENT.unique()]), columns= ['UNIQUE_SCENTS_WITHIN_THIS_CATEGORY'])\
.reset_index(drop = False).to_csv('BEAUTY_UNIQUE_SCENTS_IN_SUBCOMS.csv', index = None)